In [73]:
import re
import pandas as pd
import numpy as np
import scipy
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from pandas import Series, DataFrame
import nltk

import spacy
import string

In [92]:
df = pd.DataFrame(pd.read_csv("C:/data/CS/scraped/NEW_Aggregated_Result_2019-10-08-18-04.csv"))
df.describe()

SYMBOL      SITE_NAME  \
count                      1021            728   
unique                      119              7   
top     Shutterfly, Inc. | SFLY  Yahoo Finance   
freq                         48            252   

                                                      URL  \
count                                                1021   
unique                                                541   
top     https://finance.yahoo.com/news/delisting-secur...   
freq                                                   18   

                         PUBLISH_TIME      SCRAPED_TIME  \
count                            1021               991   
unique                            303                 5   
top     Fri, 20 Sep 2019 07:00:00 GMT  2019-10-08-18-04   
freq                               46               728   

                                                    TITLE  \
count                                                1021   
unique                                                542   
top     Delisting of Securities of Hunter Maritime Acq...   
freq                                                   18   

                                                  CONTENT  
count                                                1009  
unique                                                527  
top     NEW YORK, Sept. 20, 2019 (GLOBE NEWSWIRE) -- T...  
freq                                                   18

In [93]:
df.drop_duplicates(keep='first')
df.describe()

SYMBOL      SITE_NAME  \
count                      1021            728   
unique                      119              7   
top     Shutterfly, Inc. | SFLY  Yahoo Finance   
freq                         48            252   

                                                      URL  \
count                                                1021   
unique                                                541   
top     https://finance.yahoo.com/news/delisting-secur...   
freq                                                   18   

                         PUBLISH_TIME      SCRAPED_TIME  \
count                            1021               991   
unique                            303                 5   
top     Fri, 20 Sep 2019 07:00:00 GMT  2019-10-08-18-04   
freq                               46               728   

                                                    TITLE  \
count                                                1021   
unique                                                542   
top     Delisting of Securities of Hunter Maritime Acq...   
freq                                                   18   

                                                  CONTENT  
count                                                1009  
unique                                                527  
top     NEW YORK, Sept. 20, 2019 (GLOBE NEWSWIRE) -- T...  
freq                                                   18

In [94]:
df.head()

SYMBOL SITE_NAME  \
0  Alta Mesa Resources, Inc. | AMRWW   Reuters   
1  Alta Mesa Resources, Inc. | AMRWW   Reuters   
2  Alta Mesa Resources, Inc. | AMRWW   Reuters   
3                    Cray Inc | CRAY   Reuters   
4                    Cray Inc | CRAY   Reuters   

                                                 URL  \
0  https://www.reuters.com/article/bankruptcy-alt...   
1  https://www.reuters.com/article/bankruptcy-alt...   
2  https://www.reuters.com/article/us-oklahoma-en...   
3  https://www.reuters.com/article/us-cray-m-a-hp...   
4  https://www.reuters.com/article/us-usa-intel/p...   

                    PUBLISH_TIME      SCRAPED_TIME  \
0  Tue, 17 Sep 2019 07:00:00 GMT  2019-10-08-18-04   
1  Thu, 12 Sep 2019 07:00:00 GMT  2019-10-08-18-04   
2  Thu, 13 Jun 2019 07:00:00 GMT  2019-10-08-18-04   
3  Fri, 17 May 2019 07:00:00 GMT  2019-10-08-18-04   
4  Mon, 18 Mar 2019 07:00:00 GMT  2019-10-08-18-04   

                                               TITLE  \
0  IN BRIEF: Alta Mesa mulls adding midstream aff...   
1  Alta Mesa files for Ch. 11, looking for buyer ...   
2  Interest dims in Oklahoma shale play as drilli...   
3  Hewlett Packard Enterprise to buy supercompute...   
4  Project Aurora: U.S. government, Intel aim for...   

                                             CONTENT  
0  Energy producer Alta Mesa Resources Inc has pr...  
1  Energy producer Alta Mesa Resources Inc has fi...  
2  NEW YORK (Reuters) - It promised to be the nex...  
3  A trader passes by the post where Hewlett Pack...  
4  (Reuters) - A U.S. government-led group is wor...

In [95]:
df.dropna(subset=['SYMBOL'], inplace=True)
df.describe()

SYMBOL      SITE_NAME  \
count                      1021            728   
unique                      119              7   
top     Shutterfly, Inc. | SFLY  Yahoo Finance   
freq                         48            252   

                                                      URL  \
count                                                1020   
unique                                                540   
top     https://www.globenewswire.com/news-release/201...   
freq                                                   18   

                         PUBLISH_TIME      SCRAPED_TIME  \
count                            1020               990   
unique                            302                 5   
top     Fri, 20 Sep 2019 07:00:00 GMT  2019-10-08-18-04   
freq                               46               728   

                                                    TITLE  \
count                                                1020   
unique                                                541   
top     Delisting of Securities of Hunter Maritime Acq...   
freq                                                   18   

                                                  CONTENT  
count                                                1008  
unique                                                526  
top     NEW YORK, Sept. 20, 2019 (GLOBE NEWSWIRE) -- T...  
freq                                                   18

In [96]:
df.dropna(subset=['CONTENT'], inplace=True)
df.describe()

SYMBOL      SITE_NAME  \
count                      1008            716   
unique                      118              7   
top     Shutterfly, Inc. | SFLY  Yahoo Finance   
freq                         48            250   

                                                      URL  \
count                                                1008   
unique                                                534   
top     https://www.globenewswire.com/news-release/201...   
freq                                                   18   

                         PUBLISH_TIME      SCRAPED_TIME  \
count                            1008               978   
unique                            302                 5   
top     Fri, 20 Sep 2019 07:00:00 GMT  2019-10-08-18-04   
freq                               46               716   

                                                    TITLE  \
count                                                1008   
unique                                                535   
top     Delisting of Securities of Hunter Maritime Acq...   
freq                                                   18   

                                                  CONTENT  
count                                                1008  
unique                                                526  
top     NEW YORK, Sept. 20, 2019 (GLOBE NEWSWIRE) -- T...  
freq                                                   18

In [97]:
content=df['CONTENT']
content

0       Energy producer Alta Mesa Resources Inc has pr...
1       Energy producer Alta Mesa Resources Inc has fi...
2       NEW YORK (Reuters) - It promised to be the nex...
3       A trader passes by the post where Hewlett Pack...
4       (Reuters) - A U.S. government-led group is wor...
5       WASHINGTON (Reuters) - The U.S. Commerce Depar...
6       (Reuters) - Fred’s Inc FRED.O said on Monday i...
7       Sept 9 (Reuters) - Fred’s Inc said on Monday i...
8       Discount retailer Fred’s Inc sought court appr...
9       (Reuters) - Fred’s Inc said on Thursday it wou...
10      (For a live blog on the U.S. stock market, cli...
11      Energy producer Alta Mesa Resources Inc has pr...
12      Energy producer Alta Mesa Resources Inc has fi...
13      NEW YORK (Reuters) - It promised to be the nex...
14      (Reuters) - Del Frisco’s Restaurant Group Inc ...
15      (Reuters) - Del Frisco’s Restaurant Group Inc ...
16      (Reuters) - Del Frisco’s Restaurant Group Inc ...
17      (Reute

In [98]:
#function to remove non-ascii characters
def _removeNonAscii(s): return "".join(i for i in s if ord(i)<128)

In [99]:
content = content.astype('str')
#remove non-ascii characters
content = content.map(lambda x: _removeNonAscii(x))
STOPWORDS_DICT = {lang: set(nltk.corpus.stopwords.words(lang)) for lang in nltk.corpus.stopwords.fileids()}


In [100]:
#function to detect language based on # of stop words for particular language
def get_language(text):
    words = set(nltk.wordpunct_tokenize(text.lower()))
    lang = max(((lang, len(words & stopwords)) for lang, stopwords in STOPWORDS_DICT.items()), key = lambda x: x[1])[0]
    if lang == 'english':
        return True
    else:
        return False

In [101]:
#filter for only english comments
eng_content=content[content.apply(get_language)]

In [102]:
#load spacy
nlp = spacy.load('en', disable=['parser','ner'])


In [103]:
#function to clean and lemmatize comments
def clean_content(text):
    #remove punctuations
    regex = re.compile('[' + re.escape(string.punctuation) + '\\r\\t\\n]')
    nopunct = regex.sub(" ", str(text))
    #use spacy to lemmatize comments
    doc = nlp(nopunct)
    lemma = [token.lemma_ for token in doc]
    return lemma

In [104]:
#apply function to clean and lemmatize comments
lemmatized = eng_content.map(clean_content)
#make sure to lowercase everything
#make sure to lowercase everything
df['CONTENT'] = lemmatized.map(lambda x: [word.lower() for word in x])


In [105]:
df['CONTENT'][4]

[' ',
 'reuters',
 '   ',
 'a',
 'u',
 's',
 ' ',
 'government',
 'lead',
 'group',
 'be',
 'work',
 'with',
 'chipmaker',
 'intel',
 'corp',
 'and',
 'cray',
 'inc',
 'to',
 'develop',
 'and',
 'build',
 'the',
 'nation',
 'fast',
 'computer',
 'by',
 '2021',
 'for',
 'conduct',
 'nuclear',
 'weapon',
 'and',
 'other',
 'research',
 ' ',
 'official',
 'say',
 'on',
 'monday',
 '    ',
 'file',
 'photo',
 ' ',
 'intel',
 's',
 'logo',
 'be',
 'picture',
 'during',
 'preparation',
 'at',
 'the',
 'cebit',
 'computer',
 'fair',
 ' ',
 'which',
 'will',
 'open',
 '-pron-',
 'door',
 'to',
 'the',
 'public',
 'on',
 'march',
 '20',
 ' ',
 'at',
 'the',
 'fairground',
 'in',
 'hanover',
 ' ',
 'germany',
 ' ',
 'march',
 '19',
 ' ',
 '2017',
 ' ',
 'reuters',
 'fabian',
 'bimmer',
 '   ',
 'the',
 'department',
 'of',
 'energy',
 'and',
 'the',
 'argonne',
 'national',
 'laboratory',
 'near',
 'chicago',
 'say',
 '-pron-',
 'be',
 'work',
 'on',
 'a',
 'supercomputer',
 'dub',
 'aurora',
 '

In [106]:
df.dropna(subset=['CONTENT'], inplace=True)
df.head()

SYMBOL SITE_NAME  \
0  Alta Mesa Resources, Inc. | AMRWW   Reuters   
1  Alta Mesa Resources, Inc. | AMRWW   Reuters   
2  Alta Mesa Resources, Inc. | AMRWW   Reuters   
3                    Cray Inc | CRAY   Reuters   
4                    Cray Inc | CRAY   Reuters   

                                                 URL  \
0  https://www.reuters.com/article/bankruptcy-alt...   
1  https://www.reuters.com/article/bankruptcy-alt...   
2  https://www.reuters.com/article/us-oklahoma-en...   
3  https://www.reuters.com/article/us-cray-m-a-hp...   
4  https://www.reuters.com/article/us-usa-intel/p...   

                    PUBLISH_TIME      SCRAPED_TIME  \
0  Tue, 17 Sep 2019 07:00:00 GMT  2019-10-08-18-04   
1  Thu, 12 Sep 2019 07:00:00 GMT  2019-10-08-18-04   
2  Thu, 13 Jun 2019 07:00:00 GMT  2019-10-08-18-04   
3  Fri, 17 May 2019 07:00:00 GMT  2019-10-08-18-04   
4  Mon, 18 Mar 2019 07:00:00 GMT  2019-10-08-18-04   

                                               TITLE  \
0  IN BRIEF: Alta Mesa mulls adding midstream aff...   
1  Alta Mesa files for Ch. 11, looking for buyer ...   
2  Interest dims in Oklahoma shale play as drilli...   
3  Hewlett Packard Enterprise to buy supercompute...   
4  Project Aurora: U.S. government, Intel aim for...   

                                             CONTENT  
0  [energy, producer, alta, mesa, resources, inc,...  
1  [energy, producer, alta, mesa, resources, inc,...  
2  [new, york,  , reuters,    , -pron-, promise, ...  
3  [a, trader, pass, by, the, post, where, hewlet...  
4  [ , reuters,    , a, u, s,  , government, lead...

In [107]:
original_text=[]
for i in df['CONTENT']:
    ww=','.join(i)
    www=ww.replace(',',' ')
    original_text.append(www)
original_text



['energy producer alta mesa resources inc have propose sell -pron- at an auction in early january potentially along with a midstream affiliate -pron- exclude from the chapter 11 bankruptcy -pron- begin last week      alta mesa in a motion on monday in u s   bankruptcy court in houston seek an order approve bidding procedure for -pron- and -pron- kingfisher midstream llc affiliate      to read the full story on westlawnext practitioner insights   click here   bit ly 2lslrmh',
 'energy producer alta mesa resources inc have file for bankruptcy protection to try to find a buyer or restructure -pron- nearly   850 million in debt   blame weak oil price      alta mesa in paper file on thursday in u s   bankruptcy court in houston say that in addition to -pron- financial trouble   -pron- have be have to contend with substantial turnover of top executive and an investigation by the u s   securities and exchange commission into -pron- reserve estimate      to read the full story on westlawnext p

In [109]:
df['CONTENT']=original_text
print (df['CONTENT'][1])
df.describe()
dv=df
dv.describe()

energy producer alta mesa resources inc have file for bankruptcy protection to try to find a buyer or restructure -pron- nearly   850 million in debt   blame weak oil price      alta mesa in paper file on thursday in u s   bankruptcy court in houston say that in addition to -pron- financial trouble   -pron- have be have to contend with substantial turnover of top executive and an investigation by the u s   securities and exchange commission into -pron- reserve estimate      to read the full story on westlawnext practitioner insights   click here   bit ly 2kklu8z


SYMBOL      SITE_NAME  \
count                      1006            716   
unique                      117              7   
top     Shutterfly, Inc. | SFLY  Yahoo Finance   
freq                         48            250   

                                                      URL  \
count                                                1006   
unique                                                532   
top     https://www.globenewswire.com/news-release/201...   
freq                                                   18   

                         PUBLISH_TIME      SCRAPED_TIME  \
count                            1006               976   
unique                            301                 5   
top     Fri, 20 Sep 2019 07:00:00 GMT  2019-10-08-18-04   
freq                               46               716   

                                                    TITLE  \
count                                                1006   
unique                                                533   
top     Delisting of Securities of Hunter Maritime Acq...   
freq                                                   18   

                                                  CONTENT  
count                                                1006  
unique                                                525  
top     new york   sept   20   2019   globe newswire  ...  
freq                                                   18

In [110]:
df=df.drop_duplicates(subset=['CONTENT'], keep='first')
#df=df.drop_duplicates(subset=['URL'], keep='first')
df.describe()

SYMBOL      SITE_NAME  \
count     525            267   
unique    107              7   
top       AMR  Yahoo Finance   
freq       24             94   

                                                      URL  \
count                                                 525   
unique                                                522   
top     https://finance.yahoo.com/news/hedge-funds-thi...   
freq                                                    2   

                         PUBLISH_TIME      SCRAPED_TIME  \
count                             525               495   
unique                            300                 5   
top     Tue, 24 Sep 2019 07:00:00 GMT  2019-10-08-18-04   
freq                               10               267   

                                                    TITLE  \
count                                                 525   
unique                                                522   
top     A Healthy Appetite for Big-Box Stores (and Chi...   
freq                                                    2   

                                                  CONTENT  
count                                                 525  
unique                                                525  
top     for more market and invest content check out  ...  
freq                                                    1

In [112]:
df.to_csv("C:/data/CS/scraped/10102019_news_scraping_results.csv")